<h2>Using Pandas, Bokeh, and Networkx to Visualize Twitter Social Network Graph</h2>

<p>In this example, we show how Bokeh can work with Networkx graphs to add some useful interactivity. We will be using a dataset similar to the one used in the lesson on plotting Twitter data for the #muellereport, but it is much smaller. This dataset was created using the Twitter Streaming API with the hashtag "climatechange". It was collected in late 2018 when the U.S. government released its annual report on climate change. Here are some stats:</p>

In [6]:
# import packages
import pandas as pd
import datetime
import networkx as nx
import matplotlib.pyplot as plt
from bokeh.models.graphs import from_networkx
from bokeh.io import show, output_file
from bokeh.plotting import figure
from pprint import pprint

## Read the #climatechange Adjacency List for Networkx
Next, let's generate a network in networkx and perform some centrality calculations. For this lesson, we have already created a basic adjacency list by extracting the source nodes ('screen_name' parameter) and the target nodes (the 'retweeted_status->screen_name' parameter) for each retweet.

In [7]:
adjacency_list_df = pd.read_csv('data/csv/climatechange_edge_list_min5.csv')

In [8]:
adjacency_list_df.head()

source         target  weight
0  0h5ow9nuAFw0lpA     Greenpeace       5
1           1104Bj     Greenpeace      13
2           1104Bj   GreenpeaceCA       7
3           1104Bj  envirodefence       6
4           128TCC         UNFCCC      11

Now let's create the networkx graph from the adjacency list. 

In [9]:
G = nx.from_pandas_edgelist(adjacency_list_df)

## Graph Visualization With networkx
First, let's create an example of what networkx graph visualization is like. Networkx does support graph visualization but does not provide a very functional set of visualization options compared to some other graph viz programs such as Gephi. The code below will generate a graph for the #climatechange network for which we imported the adjacency list above. Depending on the size of the network and processing capabilities of your system, this could take a very long time. To reduce the time required, our adjacency list includes only those users who retweeted another users tweets 5 or more times. 

In [10]:
pprint("Start:" + str(datetime.datetime.now()))
plt.figure(figsize=(150, 150))
nx.draw_networkx(G, with_labels=True)
plt.savefig('images/climatechange_graph_network_viz2.png')
pprint("End:" + str(datetime.datetime.now()))

'Start:2019-12-11 20:46:51.371897'


/Users/jsale/anaconda3/lib/python3.7/site-packages/networkx/drawing/nx_pylab.py:611: MatplotlibDeprecationWarning: isinstance(..., numbers.Number)
  if cb.is_numlike(alpha):


'End:2019-12-11 20:48:43.694803'


## Graph Visualization With Bokeh
Now, let's create an example of what Bokeh can add in terms of interactivity to a networkx graph, including a hover tool to reveal node information, panning and zooming, saving, etc. 

In [11]:
import networkx as nx

from bokeh.io import show, output_file
from bokeh.models import Plot, Range1d, MultiLine, Circle, HoverTool, BoxZoomTool, ResetTool, WheelZoomTool
from bokeh.models.graphs import from_networkx
from bokeh.palettes import Spectral4

# Prepare Data
# G = nx.karate_club_graph()

EDGE_COLOR = "black"
edge_attrs = {}

for start_node, end_node, _ in G.edges(data=True):
    edge_color = EDGE_COLOR
    edge_attrs[(start_node, end_node)] = edge_color

nx.set_edge_attributes(G, edge_attrs, "edge_color")

# Show with Bokeh
plot = Plot(plot_width=1200, plot_height=1200,
            x_range=Range1d(-1.1, 1.1), y_range=Range1d(-1.1, 1.1))
plot.title.text = "Graph Interaction Demonstration"

node_hover_tool = HoverTool(tooltips=[("User", "@index")])
plot.add_tools(node_hover_tool, BoxZoomTool(), ResetTool(), WheelZoomTool())

graph_renderer = from_networkx(G, nx.spring_layout, scale=1, center=(0, 0))

graph_renderer.node_renderer.glyph = Circle(size=10, fill_color=Spectral4[0])
graph_renderer.edge_renderer.glyph = MultiLine(line_color="edge_color", line_alpha=0.8, line_width=1)
plot.renderers.append(graph_renderer)

output_file("climatechange_interactive_graph.html")
show(plot)